# ipython-neo4j Demo Notebook

Demonstrates `%cypher`, `%%cypher`, `%wcypher` and `%%wcypher` magic commands
against the public **Movies** demo database on `demo.neo4jlabs.com`.


In [25]:
## Setup
!pip install -q ipython-neo4j

In [26]:
%load_ext ipython_neo4j

The ipython_neo4j extension is already loaded. To reload it, use:
  %reload_ext ipython_neo4j


## 1. Connect

Connect using the `%neo4j` magic. You can also set `NEO4J_URI / NEO4J_USERNAME / NEO4J_PASSWORD / NEO4J_DATABASE` environment variables and call `%neo4j` with no arguments.

In [3]:
%neo4j neo4j+s://demo.neo4jlabs.com -u movies -p movies -d movies

In [4]:
%neo4j --status

## 2. Line magic — simple queries

In [5]:
%cypher MATCH (m:Movie) RETURN m.title AS title, m.released AS released ORDER BY released DESC LIMIT 10

CypherResult(10 rows × 2 cols, query_type='r')

## 3. Cell magic — multi-line queries

> **Note:** `%%cypher` (or any cell magic) must be the very first token of the cell.

In [6]:
%%cypher
MATCH (p:Person)-[:ACTED_IN]->(m:Movie)
RETURN p.name AS actor, count(m) AS movies
ORDER BY movies DESC
LIMIT 10

CypherResult(10 rows × 2 cols, query_type='r')

## 4. Store result in a variable

In [7]:
%%cypher -o actors
MATCH (p:Person)-[:ACTED_IN]->(m:Movie)
RETURN p.name AS name, m.title AS movie, m.released AS released
LIMIT 20

In [8]:
print(type(actors))
print(repr(actors))

<class 'ipython_neo4j.result.CypherResult'>
CypherResult(20 rows × 3 cols, query_type='r')


## 5. Get a DataFrame directly (`--df`)

In [9]:
%%cypher --df -o movies_df
MATCH (m:Movie)
RETURN m.title AS title, m.released AS released, m.tagline AS tagline
ORDER BY released DESC
LIMIT 20

In [10]:
print(type(movies_df))
movies_df.head(5)

<class 'pandas.DataFrame'>


title  released  \
0           Cloud Atlas      2012   
1        Ninja Assassin      2009   
2           Frost/Nixon      2008   
3           Speed Racer      2008   
4  Charlie Wilson's War      2007   

                                             tagline  
0                            Everything is connected  
1       Prepare to enter a secret world of assassins  
2     400 million people were waiting for the truth.  
3                                Speed has no limits  
4  A stiff drink. A little mascara. A lot of nerv...

In [11]:
# CypherResult.df shorthand
actors.df.head(5)

name       movie  released
0         Emil Eifrem  The Matrix      1999
1        Hugo Weaving  The Matrix      1999
2  Laurence Fishburne  The Matrix      1999
3    Carrie-Anne Moss  The Matrix      1999
4        Keanu Reeves  The Matrix      1999

## 6. Parameterised queries (`-P`)

The `-P` expression is `eval()`'d in the notebook namespace,
so you can reference any variable as the params dict.

In [12]:
params = {"year": 2000, "name": "Tom Hanks"}

In [13]:
%%cypher -P params -o hanks_movies
MATCH (p:Person {name: $name})-[:ACTED_IN]->(m:Movie)
WHERE m.released >= $year
RETURN m.title AS title, m.released AS released
ORDER BY released

Received notification from DBMS server: <GqlStatusObject gql_status='01N60', status_description="warn: parameter missing. The query plan cannot be cached and is not executable without 'EXPLAIN' due to the undefined parameter(s) $`name` and $`year`. Provide the parameter(s).", position=None, raw_classification='GENERIC', classification=<NotificationClassification.GENERIC: 'GENERIC'>, raw_severity='WARNING', severity=<NotificationSeverity.WARNING: 'WARNING'>, diagnostic_record={'_classification': 'GENERIC', '_severity': 'WARNING', 'OPERATION': '', 'OPERATION_CODE': '0', 'CURRENT_SCHEMA': '/'}> for query: 'EXPLAIN MATCH (p:Person {name: $name})-[:ACTED_IN]->(m:Movie)\nWHERE m.released >= $year\nRETURN m.title AS title, m.released AS released\nORDER BY released'


In [14]:
hanks_movies.df

title  released
0             Cast Away      2000
1     The Polar Express      2004
2     The Da Vinci Code      2006
3  Charlie Wilson's War      2007
4           Cloud Atlas      2012

## 7. Read/Write safety

`%cypher` runs an `EXPLAIN` pre-flight and **blocks write queries by default**.
Use `%%cypher --write` or `%%wcypher` to explicitly allow writes.

In [15]:
# EXPLAIN detects this as a write — it is blocked
%cypher CREATE (n:TestNode {name: 'should be blocked'}) RETURN n

In [16]:
%%cypher --no-preflight
MATCH (m:Movie) RETURN m.title AS title LIMIT 3

CypherResult(3 rows × 1 cols, query_type='r')

## 8. Graph visualization with neo4j-viz (`--viz`)

Return `Node` and `Relationship` objects — the result is rendered as an interactive graph.

In [17]:
%%cypher --viz
MATCH (p:Person)-[r:ACTED_IN]->(m:Movie)
RETURN p, r, m
LIMIT 30

/Users/mh/d/python/ipython-neo4j/.venv/lib/python3.13/site-packages/neo4j_viz/visualization_graph.py:765: UserWarning: Ran out of colors for property 'caption'. 27 colors were needed, but only 12 were given, so reused colors
  warnings.warn(


In [18]:
%%cypher -o graph_result
MATCH (p:Person)-[r:DIRECTED]->(m:Movie)
RETURN p, r, m
LIMIT 20

In [19]:
# Programmatic visualization
graph_result.visualize(color_by="caption")

/Users/mh/d/python/ipython-neo4j/.venv/lib/python3.13/site-packages/neo4j_viz/visualization_graph.py:765: UserWarning: Ran out of colors for property 'caption'. 30 colors were needed, but only 12 were given, so reused colors
  warnings.warn(


## 9. Error rendering

Neo4j exceptions are rendered as styled HTML, not raw Python tracebacks.

In [20]:
%cypher MATCH (n) RETURN @@invalid@@

## 10. Per-query connection override

In [21]:
%%cypher -u neo4j+s://demo.neo4jlabs.com --username movies -p movies -d movies
MATCH (m:Movie) RETURN m.title AS title LIMIT 3

CypherResult(3 rows × 1 cols, query_type='r')

## 11. Disconnect

In [22]:
%neo4j --close